In [1]:
import numpy as np
import math 
import cmath
import abipy
from abipy.electrons.scr import ScrFile
import time
import matplotlib.pyplot as plt
import pointcloud as pc
from scipy.interpolate import RegularGridInterpolator
import plotly.graph_objects as go
%load_ext autoreload
%autoreload 2
import Fourier_tool as Ft
import XGChi0 
import MatrixCharacteristic
from abipy import abilab
import abipy.data as abidata
from abipy.abilab import Structure
import random


## List of available matrices : 

### Reciprocal space

- chi0GG_conv_eps6_FromSym_ngkpt444_omega0_nband150.npy
- chi0GG_prim_eps3_6_FromSym_ngkpt888_omega0_nband150.npy
- chi0GG_prim_eps5_FromSym_ngkpt444_omega0_nband150.npy
- chi0GG_prim_eps5_FromSym_ngkpt666_omega0_nband150.npy
- chi0GG_prim_eps9_FromSym_ngkpt444_omega0_nband100.npy
- chi0GG_prim_eps9_FromSym_ngkpt444_omega0_nband150.npy
- chi0GG_prim_eps9_FromSym_ngkpt444_omega0_nband200.npy
- chi0GG_prim_eps9_FromSym_ngkpt444_omega0_nband250.npy
- chi0GG_prim_eps9_FromSym_ngkpt444_omega0_nband300.npy
- chi0GG_prim_eps13_FromSym_ngkpt444_omega0_nband150.npy
- chi0GG_prim_eps17_FromSym_ngkpt444_omega0.npy
- chi0GG_prim_eps17_FromSym_ngkpt888_omega0.npy
- chi0GG_prim_eps17_FromSym_ngkpt101010_omega0_nband150.npy
- chi0GG_prim_eps21_FromSym_ngkpt444_omega0_nband150.npy
- chi0GG_prim_eps25_FromSym_ngkpt444_omega0_nband150.npy
- chi0GG_slab13_eps14_FromSym_ngkpt441_omega0_nband150.npy
- chi0GG_Conv_eps14_FromSym_ngkpt444_omega0_nband150.npy (file : Al_Bulk_GSo_DS1_SUS.nc)
- chi0GG_slab4_eps14_FromSym_ngkpt441_omega0_nband150.npy


### Direct space

- chi0rr_conv_eps3_6_FromSym_ngkpt888_omega0_nband150.npy
- chi0rr_conv_eps5_FromSym_ngkpt666_omega0_nband150.npy
- chi0rr_conv_eps6_FromSym_ngkpt444_omega0_nband150.npy
- chi0rr_prim_eps5_FromSym_ngkpt444_omega0_nband150.npy
- chi0rr_prim_eps9_FromSym_ngkpt444_omega0_nband100.npy
- chi0rr_prim_eps9_FromSym_ngkpt444_omega0_nband150.npy
- chi0rr_prim_eps9_FromSym_ngkpt444_omega0_nband200.npy
- chi0rr_prim_eps9_FromSym_ngkpt444_omega0_nband250.npy
- chi0rr_prim_eps9_FromSym_ngkpt444_omega0_nband300.npy
- chi0rr_prim_eps13_FromSym_ngkpt444_omega0_nband150.npy
- chi0rr_prim_eps17_FromSym_ngkpt444_omega0.npy
- chi0rr_prim_eps17_FromSym_ngkpt888_omega0.npy
- chi0rr_prim_eps21_FromSym_ngkpt444_omega0_nband150.npy
- chi0rr_prim_eps25_FromSym_ngkpt444_omega0_nband150.npy
- chi0rr_slab13_eps14_FromSym_ngkpt441_omega0_nband150.npy
- chi0rr_Conv_eps14_FromSym_ngkpt444_omega0_nband150.npy (file : Al_Bulk_GSo_DS1_SUS.nc)
- chi0rr_slab4_eps14_FromSym_ngkpt441_omega0_nband150.npy

# Data about the inputs

In [178]:
filename = "Al_Bulk_nkpt4o_DS1_SUS.nc"
MatGG = "chi0GG_Conv_eps14_FromSym_ngkpt444_omega0_nband150.npy"
Matrr = "chi0rr_Conv_eps14_FromSym_ngkpt444_omega0_nband150.npy"
ngkpt = [4, 4, 4] #has to be entered manually from the data given above
nsym_var = 0

In [175]:
structure=abipy.core.structure.Structure.from_file(filename)
structure
#structure.visualize("vesta")

Structure Summary
Lattice
    abc : 2.8535866547158504 2.8535866547158504 2.8535866547158504
 angles : 59.999999999999986 59.99999999999999 59.99999999999999
 volume : 16.430780655166938
      A : 1.6475190232561199 0.0 2.3299437469564794
      B : -0.8237595116280599 1.426793327357925 2.3299437469564794
      C : -0.8237595116280599 -1.426793327357925 2.3299437469564794
PeriodicSite: Al (0.0000, 0.0000, 0.0000) [0.0000, 0.0000, 0.0000]

In [176]:
dict_struct = structure.to_abivars()
natom = dict_struct["natom"]
xred = dict_struct["xred"]
lattice = structure.lattice.matrix
A, B, C = lattice[0], lattice[1], lattice[2]

In [154]:
XGChi0.Supercell_Vis(A, B, C, ngkpt, natom, xred)

In [169]:
XGChi0.Supercell_Vis(A, B, C, ngkpt, natom, xred)

In [173]:
XGChi0.Supercell_Vis(A, B, C, ngkpt, natom, xred)

In [179]:
XGChi0.Supercell_Vis(A, B, C, ngkpt, natom, xred)

# Information about the reconstructed matrix

In [6]:
chi0GG = np.load(MatGG)

In [7]:
chi0GG_const = chi0GG[0, 0, 0]
sum_chi0GG = np.sum(chi0GG)
sum_norm_chi0GG = np.sum(np.abs(np.power(np.real(chi0GG), 2))),np.sum(np.abs(np.power(np.imag(chi0GG),2)))
#sum_abs_chi0GG = complex(np.sum(np.abs(np.real(chi0GG))),np.sum(np.abs(np.imag(chi0GG))))
max_r_chi0GG = np.max(np.abs(np.real(chi0GG)))
max_i_chi0GG = np.max(np.abs(np.imag(chi0GG)))

In [8]:
print("The constant component = ", chi0GG_const,"\nThe sum of all the components = ", sum_chi0GG,"\nThe sum of the norm of all components = ", sum_norm_chi0GG, "\nThe maximum absolute real value = ", max_r_chi0GG, "\nThe maximum absolute imaginary value = ", max_i_chi0GG,"\nThe shape of the matrix = ", chi0GG.shape)

The constant component =  (-5.972790262376293e-09+4.710217590852708e-26j) 
The sum of all the components =  (-2.6983802495612244+2.571870411049164e-09j) 
The sum of the norm of all components =  (23.74262418424471, 0.0023243191399856407) 
The maximum absolute real value =  0.10738244652748108 
The maximum absolute imaginary value =  0.0029017881024628878 
The shape of the matrix =  (64, 1141, 1141)


# Information about the direct space matrix

In [19]:
chi0rr = np.load(Matrr)

In [10]:
chi0rr_origin = chi0rr[0, 0, 0, 0, 0, 0]
sum_chi0rr = np.sum(chi0rr)
sum_per_pert = sum_chi0rr/chi0rr.size
sum_norm_chi0rr = np.sum(np.abs(np.power(np.real(chi0rr), 2))),np.sum(np.abs(np.power(np.imag(chi0rr),2)))
#sum_abs_chi0GG = complex(np.sum(np.abs(np.real(chi0GG))),np.sum(np.abs(np.imag(chi0GG))))
max_r_chi0rr = np.max(np.abs(np.real(chi0rr)))
max_i_chi0rr = np.max(np.abs(np.imag(chi0rr)))

In [11]:
print("The origin component = ", chi0rr_origin,"\nThe sum of all the components = ", sum_chi0rr, "\nThe average variation of the density for a given perturbation of 1 =", sum_per_pert, "\nThe sum of the norm of all components = ", sum_norm_chi0rr, "\nThe maximum absolute real value = ", max_r_chi0rr, "\nThe maximum absolute imaginary value = ", max_i_chi0rr,"\nThe shape of the matrix = ", chi0rr.shape)

The origin component =  (-2.698380249561217+2.5718704069698473e-09j) 
The sum of all the components =  (-3.174185629866031+5.808686864838819e-12j) 
The average variation of the density for a given perturbation of 1 = (-5.972790262448759e-09+1.0930069123080113e-20j) 
The sum of the norm of all components =  (12220515638.807056, 398523538.77993935) 
The maximum absolute real value =  588.5760689073397 
The maximum absolute imaginary value =  38.25490123453463 
The shape of the matrix =  (15, 15, 15, 54, 54, 54)


# Visualisation tools

In [21]:
n1_go, n2_go, n3_go, n4_go, n5_go, n6_go = chi0rr.shape
print(chi0rr.shape)

(15, 15, 15, 54, 54, 54)


In [22]:
X1 = np.linspace(0, ngkpt[0], n4_go,endpoint = False)
X2 = np.linspace(0, ngkpt[1], n5_go,endpoint = False)
X3 = np.linspace(0, ngkpt[2], n6_go,endpoint = False)

X1R = np.linspace(0, 1, n1_go, endpoint = False)
X2R = np.linspace(0, 1, n2_go, endpoint = False)
X3R = np.linspace(0, 1, n3_go, endpoint = False)

Y1 = np.real(chi0rr[0,0,0,:,0,0])
Y2 = np.real(chi0rr[0,0,0,0,:,0])
Y3 = np.real(chi0rr[0,0,0,0,0,:])

Y1R = np.real(chi0rr[:,0,0,0,0,0])
Y2R = np.real(chi0rr[0,:,0,0,0,0])
Y3R = np.real(chi0rr[0,0,:,0,0,0])

In [14]:
trace1 = go.Scatter(
                    x = X1,
                    y = Y1,
                    mode = "lines+markers",
                    name = "Axe0"
                    )

trace2 = go.Scatter(
                    x = X2,
                    y = Y2,
                    mode = "lines+markers",
                    name = "Axe1"
                    )

trace3 = go.Scatter(
                    x = X3,
                    y = Y3,
                    mode = "lines+markers",
                    name = "Axe2"
                    )

trace4 = go.Scatter(
                    x = X1R,
                    y = Y1R,
                    mode = "lines+markers",
                    name = "Axe0K"
                    )

trace5 = go.Scatter(
                    x = X2R,
                    y = Y2R,
                    mode = "lines+markers",
                    name = "Axe1K"
                    )

trace6 = go.Scatter(
                    x = X3R,
                    y = Y3R,
                    mode = "lines+markers",
                    name = "Axe2K"
                    )



data = [trace1, trace2, trace3, trace4, trace5, trace6]
layout = dict(title = '\chi^0(r, r\') with r_red ='+str([0, 0, 0])+' for different directions',
              xaxis= dict(title= 'Number of unit cells',ticklen= 5,zeroline= False),
             )
fig = go.Figure(dict(data = data, layout = layout))
fig.show()

In [17]:
R = [0, 0, 0]

In [21]:
XGChi0.Vis_tool(chi0rr, R, A, B, C, ngkpt, natom, xred, N=10000, isomin=0)

In [15]:
R_2D = [3, 3, 6]

In [16]:
X1_2D = np.linspace(0, ngkpt[0], n4_go,endpoint = False)
X2_2D = np.linspace(0, ngkpt[1], n5_go,endpoint = False)
X3_2D = np.linspace(0, ngkpt[2], n6_go,endpoint = False)

Y1_2D = np.real(chi0rr[R_2D[0], R_2D[1], R_2D[2], :, R_2D[1], R_2D[2]])
Y2_2D = np.real(chi0rr[R_2D[0], R_2D[1], R_2D[2], R_2D[0], :, R_2D[2]])
Y3_2D = np.real(chi0rr[R_2D[0], R_2D[1], R_2D[2], R_2D[0], R_2D[1], :])



Y4_2D = np.real(chi0rr[R_2D[0], R_2D[1], R_2D[2], :, 0, 0])
Y5_2D = np.real(chi0rr[R_2D[0], R_2D[1], R_2D[2], 0, :, 0])
Y6_2D = np.real(chi0rr[R_2D[0], R_2D[1], R_2D[2], 0, 0, :])

Y1_2DK = np.real(chi0rr[:, R_2D[1], R_2D[2], R_2D[0], R_2D[1], R_2D[2]])
Y2_2DK = np.real(chi0rr[R_2D[0], :, R_2D[2], R_2D[0], R_2D[1], R_2D[2]])
Y3_2DK = np.real(chi0rr[R_2D[0], R_2D[1], :, R_2D[0], R_2D[1], R_2D[2]])

In [17]:
trace1 = go.Scatter(
                    x = X1_2D,
                    y = Y1_2D,
                    mode = "lines+markers",
                    name = "Axe0"
                    )

trace2 = go.Scatter(
                    x = X2_2D,
                    y = Y2_2D,
                    mode = "lines+markers",
                    name = "Axe1"
                    )

trace3 = go.Scatter(
                    x = X3_2D,
                    y = Y3_2D,
                    mode = "lines+markers",
                    name = "Axe2"
                    )

trace4 = go.Scatter(
                    x = X1_2D,
                    y = Y4_2D,
                    mode = "lines+markers",
                    name = "Axe0_origin"
                    )

trace5 = go.Scatter(
                    x = X2_2D,
                    y = Y5_2D,
                    mode = "lines+markers",
                    name = "Axe1_origin"
                    )

trace6 = go.Scatter(
                    x = X3_2D,
                    y = Y6_2D,
                    mode = "lines+markers",
                    name = "Axe2_origin"
                    )

trace7 = go.Scatter(
                    x = X1R,
                    y = Y1_2DK,
                    mode = "lines+markers",
                    name = "Axe0K"
                    )

trace8 = go.Scatter(
                    x = X2R,
                    y = Y2_2DK,
                    mode = "lines+markers",
                    name = "Axe1K"
                    )

trace9 = go.Scatter(
                    x = X3R,
                    y = Y3_2DK,
                    mode = "lines+markers",
                    name = "Axe2K"
                    )



data = [trace1, trace2, trace3, trace4, trace5, trace6, trace7, trace8, trace9]
layout = dict(title = 'chi0(r, r\') with R ='+str(R_2D)+' for different directions',
              xaxis= dict(title= 'Number of unit cells',ticklen= 5,zeroline= False),
             )
fig = go.Figure(dict(data = data, layout = layout))
fig.show()

# Comparaison between conventionnal cell and primitive one

In [20]:
chi0rrprim = np.load("chi0rr_prim_eps13_FromSym_ngkpt444_omega0_nband150.npy")

In [23]:
n1_go_prim, n2_go_prim, n3_go_prim, n4_go_prim, n5_go_prim, n6_go_prim = chi0rrprim.shape
print(chi0rrprim.shape)

(9, 9, 9, 36, 36, 36)


In [24]:
maxprim = np.max(np.real(np.abs(chi0rrprim)))

In [25]:
Xconv = np.linspace(0, ngkpt[0]*4.03893, n4_go,endpoint = False)
Xprim = np.linspace(0, ngkpt[0]*2.853587, n4_go_prim,endpoint = False)

In [64]:
Rred = np.array([0.4, 0.5, 0.3])
Rconv = np.array(np.round(Rred * n1_go), dtype = int)
Rprim = np.array(np.round(Rred * n1_go_prim), dtype = int)

NameError: name 'n1_go_prim' is not defined

In [36]:
Yconv = np.real(chi0rr[Rconv[0], Rconv[1], Rconv[2], :, Rconv[1], Rconv[2]])/max_r_chi0rr
Yprim = np.real(chi0rrprim[Rprim[0], Rprim[1], Rprim[2], :, Rprim[1], Rprim[2]])/maxprim

In [37]:
trace1 = go.Scatter(
                    x = Xconv,
                    y = Yconv,
                    mode = "lines+markers",
                    name = "Axe0 conv"
                    )

trace2 = go.Scatter(
                    x = Xprim,
                    y = Yprim,
                    mode = "lines+markers",
                    name = "Axe0 prim"
                    )

#, trace3, trace4, trace5, trace6
data = [trace1, trace2]
layout = dict(title = '\chi^0(r, r\') with r_red ='+str(Rred)+' for different directions',
              xaxis= dict(title= 'Position in the supercell along the axe [100] [A]',ticklen= 5,zeroline= False),
             )
fig = go.Figure(dict(data = data, layout = layout))
fig.show()

# Nband comparaison

In [62]:
chi0rr = np.load("chi0rr_prim_eps9_FromSym_ngkpt444_omega0_nband150.npy")

In [63]:
chi0rrvs = np.load("chi0rr_prim_eps9_FromSym_ngkpt444_omega0_nband300.npy")

In [64]:
n1_go, n2_go, n3_go, n4_go, n5_go, n6_go = chi0rr.shape

In [65]:
R = [0, 0, 0]

In [66]:
max_r = np.max(np.abs(np.real(chi0rr)))
max_r_vs = np.max(np.abs(np.real(chi0rrvs)))

In [70]:
X = np.linspace(0, ngkpt[0], n4_go,endpoint = False)
Y = np.real(chi0rr[R[0], R[1], R[2], :, R[1], R[2]])/max_r
Yvs = np.real(chi0rrvs[R[0], R[1], R[2], :, R[1], R[2]])/max_r_vs

In [71]:
trace1 = go.Scatter(
                    x = X,
                    y = Y,
                    mode = "lines+markers",
                    name = "Axe0 nband150"
                    )

trace2 = go.Scatter(
                    x = X,
                    y = Yvs,
                    mode = "lines+markers",
                    name = "Axe0 nband300"
                    )

#, trace3, trace4, trace5, trace6
data = [trace1, trace2]
layout = dict(title = '\chi^0(r, r\') with r_red ='+str(R)+' for different directions',
              xaxis= dict(title= 'Number of unit cell',ticklen= 5,zeroline= False),
             )
fig = go.Figure(dict(data = data, layout = layout))
fig.show()

# Ecuteps comparaison

In [38]:
chi0rr = np.load("chi0rr_prim_eps9_FromSym_ngkpt444_omega0_nband150.npy")

In [39]:
chi0rrvs = np.load("chi0rr_prim_eps13_FromSym_ngkpt444_omega0_nband150.npy")

In [40]:
chi0rrvs1 = np.load("chi0rr_prim_eps17_FromSym_ngkpt444_omega0.npy")

In [41]:
chi0rrvs2 = np.load("chi0rr_prim_eps25_FromSym_ngkpt444_omega0_nband150.npy")

In [42]:
n1_go, n2_go, n3_go, n4_go, n5_go, n6_go = chi0rr.shape
n1_go1, n2_go1, n3_go1, n4_go1, n5_go1, n6_go1 = chi0rrvs.shape
n1_go2, n2_go2, n3_go2, n4_go2, n5_go2, n6_go2 = chi0rrvs1.shape
n1_go3, n2_go3, n3_go3, n4_go3, n5_go3, n6_go3 = chi0rrvs2.shape

In [43]:
max_r = np.max(np.abs(np.real(chi0rr)))
max_r_vs = np.max(np.abs(np.real(chi0rrvs)))
max_r_vs1 = np.max(np.abs(np.real(chi0rrvs1)))
max_r_vs2 = np.max(np.abs(np.real(chi0rrvs2)))

In [44]:
Rred = np.array([0, 0.5, 0.1])

In [45]:
R = np.array(np.round(Rred * n1_go), dtype = int)
Rvs = np.array(np.round(Rred * n1_go1), dtype = int)
Rvs1 = np.array(np.round(Rred * n1_go2), dtype = int)
Rvs2 = np.array(np.round(Rred * n1_go3), dtype = int)

In [46]:
print(Rvs1)

[0 4 1]


In [47]:
X = np.linspace(0, ngkpt[0], n4_go,endpoint = False)
X1 = np.linspace(0, ngkpt[0], n4_go1,endpoint = False)
X2 = np.linspace(0, ngkpt[0], n4_go2,endpoint = False)
X3 = np.linspace(0, ngkpt[0], n4_go3,endpoint = False)
Y = np.real(chi0rr[R[0], R[1], R[2], :, R[1], R[2]])/max_r
Yvs = np.real(chi0rrvs[Rvs[0], Rvs[1], Rvs[2], :, Rvs[1], Rvs[2]])/max_r_vs
Yvs1 = np.real(chi0rrvs1[Rvs1[0], Rvs1[1], Rvs1[2], :, Rvs1[1], Rvs1[2]])/max_r_vs1
Yvs2 = np.real(chi0rrvs2[Rvs2[0], Rvs2[1], Rvs2[2], :, Rvs2[1], Rvs2[2]])/max_r_vs2


In [48]:
trace1 = go.Scatter(
                    x = X,
                    y = Y,
                    mode = "lines+markers",
                    name = "Axe0 ecut9"
                    )

trace2 = go.Scatter(
                    x = X1,
                    y = Yvs,
                    mode = "lines+markers",
                    name = "Axe0 ecut13"
                    )

trace3 = go.Scatter(
                    x = X2,
                    y = Yvs1,
                    mode = "lines+markers",
                    name = "Axe0 ecut17"
                    )

trace4 = go.Scatter(
                    x = X3,
                    y = Yvs2,
                    mode = "lines+markers",
                    name = "Axe0 ecut21"
                    )

#, trace3, trace4, trace5, trace6
data = [trace1, trace2, trace3, trace4]
layout = dict(title = '\chi^0(r, r\') with r_red ='+str(R)+' for different ecut',
              xaxis= dict(title= 'Number of unit cell',ticklen= 5,zeroline= False),
             )
fig = go.Figure(dict(data = data, layout = layout))
fig.show()

# Increase of nkpt

In [118]:
chi0rr = np.load("chi0rr_prim_eps17_FromSym_ngkpt444_omega0.npy")

In [119]:
chi0rrvs = np.load("chi0rr_prim_eps17_FromSym_ngkpt888_omega0.npy")

In [120]:
chi0rrvs1 = np.load("chi0rr_prim_eps17_FromSym_ngkpt101010_omega0.npy")

In [121]:
n1_go, n2_go, n3_go, n4_go, n5_go, n6_go = chi0rr.shape
n1_go1, n2_go1, n3_go1, n4_go1, n5_go1, n6_go1 = chi0rrvs.shape
n1_go2, n2_go2, n3_go2, n4_go2, n5_go2, n6_go2 = chi0rrvs1.shape

In [122]:
max_r = np.max(np.abs(np.real(chi0rr)))
max_r_vs = np.max(np.abs(np.real(chi0rrvs)))
max_r_vs1 = np.max(np.abs(np.real(chi0rrvs1)))

In [127]:
Rred = np.array([0, 0, 0])

In [128]:
R = np.array(np.round(Rred * n1_go), dtype = int)
Rvs = np.array(np.round(Rred * n1_go1), dtype = int)
Rvs1 = np.array(np.round(Rred * n1_go2), dtype = int)

In [133]:
X = np.linspace(0, ngkpt[0], n4_go,endpoint = False)
X1 = np.linspace(0, 8, n4_go1,endpoint = False)
X2 = np.linspace(0, ngkpt[0], n4_go2,endpoint = False)
Y = np.real(chi0rr[R[0], R[1], R[2], :, R[1], R[2]])/max_r
Yvs = np.real(chi0rrvs[Rvs[0], Rvs[1], Rvs[2], :, Rvs[1], Rvs[2]])/max_r_vs
Yvs1 = np.real(chi0rrvs1[Rvs1[0], Rvs1[1], Rvs1[2], :, Rvs1[1], Rvs1[2]])/max_r_vs1

In [136]:
trace1 = go.Scatter(
                    x = X,
                    y = Y,
                    mode = "lines+markers",
                    name = "Axe0 ngkpt4"
                    )

trace2 = go.Scatter(
                    x = X1,
                    y = Yvs,
                    mode = "lines+markers",
                    name = "Axe0 ngkpt8"
                    )

""" trace3 = go.Scatter(
                    x = X,
                    y = Yvs1,
                    mode = "lines+markers",
                    name = "Axe0 ecut17"
                    ) """


#, trace3, trace4, trace5, trace6
data = [trace1, trace2]
layout = dict(title = '\chi^0(r, r\') with r_red ='+str(R)+' for different ngkpt',
              xaxis= dict(title= 'Number of unit cell',ticklen= 5,zeroline= False),
             )
fig = go.Figure(dict(data = data, layout = layout))
fig.show()

# Slab Comparaison

In [2]:
chi0rr = np.load("chi0rr_slab4_eps14_FromSym_ngkpt441_omega0_nband150.npy")

In [3]:
chi0rrvs = np.load("chi0rr_slab13_eps14_FromSym_ngkpt441_omega0_nband150.npy")

In [4]:
chi0rrvs1 = np.load("chi0rr_Conv_eps14_FromSym_ngkpt444_omega0_nband150.npy")

In [5]:
n1_go, n2_go, n3_go, n4_go, n5_go, n6_go = chi0rr.shape
n1_go1, n2_go1, n3_go1, n4_go1, n5_go1, n6_go1 = chi0rrvs.shape
n1_go2, n2_go2, n3_go2, n4_go2, n5_go2, n6_go2 = chi0rrvs1.shape

In [6]:
max_r = np.max(np.abs(np.real(chi0rr)))
max_r_vs = np.max(np.abs(np.real(chi0rrvs)))
max_r_vs1 = np.max(np.abs(np.real(chi0rrvs1)))

In [158]:
ngkpt = [4, 4, 1]

In [184]:
Rred = np.array([0, 0, 0.5])

In [185]:
R = np.array(np.round(np.multiply(Rred, [n1_go, n2_go, n3_go])), dtype = int)
Rvs = np.array(np.round(np.multiply(Rred, [n1_go1, n2_go1, n3_go1])), dtype = int)
Rvs1 = np.array(np.round(Rred * n1_go2), dtype = int)

[0 0 0]


In [186]:
X = np.linspace(0, ngkpt[0]*2.8535866547158504, n4_go,endpoint = False)
X1 = np.linspace(0, 14.124533319771093, n6_go,endpoint = False)

Xvs = np.linspace(0, ngkpt[0]*2.8535866547158504, n4_go1,endpoint = False)
Xvs1 = np.linspace(0, 32.28464758804821, n6_go1,endpoint = False)

X2 = np.linspace(0, ngkpt[0]*4.0389300176539065, n4_go2,endpoint = False)

Y = np.real(chi0rr[R[0], R[1], R[2], :, R[1], R[2]])/max_r
Y1 = np.real(chi0rr[R[0], R[1], R[2], R[0], R[1], :])/max_r

Yvs = np.real(chi0rrvs[Rvs[0], Rvs[1], Rvs[2], :, Rvs[1], Rvs[2]])/max_r_vs
Yvs1 = np.real(chi0rrvs[Rvs[0], Rvs[1], Rvs[2], Rvs[0], Rvs[1], :])/max_r_vs

Yvs2 = np.real(chi0rrvs1[Rvs1[0], Rvs1[1], Rvs1[2], :, Rvs1[1], Rvs1[2]])/max_r_vs1


In [187]:
trace1 = go.Scatter(
                    x = X,
                    y = Y,
                    mode = "lines+markers",
                    name = "Axe0 slab4"
                    )

trace2 = go.Scatter(
                    x = X1,
                    y = Y1,
                    mode = "lines+markers",
                    name = "Axe2 slab4"
                    )

trace3 = go.Scatter(
                    x = Xvs,
                    y = Yvs,
                    mode = "lines+markers",
                    name = "Axe0 slab13"
                    )

trace4 = go.Scatter(
                    x = Xvs1,
                    y = Yvs1,
                    mode = "lines+markers",
                    name = "Axe2 slab13"
                    )

trace5 = go.Scatter(
                    x = X2,
                    y = Yvs2,
                    mode = "lines+markers",
                    name = "Axe0, conv"
                    )

data = [trace1, trace2, trace3, trace4, trace5]
layout = dict(title = '\chi^0(r, r\') with r_red ='+str(Rred)+' for different number of layers and conv cell',
              xaxis= dict(title= 'Distance from origin',ticklen= 5,zeroline= False),
             )
fig = go.Figure(dict(data = data, layout = layout))
fig.show()

In [150]:
XGChi0.Vis_tool(chi0rr, R, A, B, C, ngkpt, natom, xred, N=10000, isomin=0)

In [136]:
dict_struct = structure.to_abivars()
natomvs = dict_struct["natom"]
xredvs = dict_struct["xred"]
latticevs = structure.lattice.matrix
Avs, Bvs, Cvs = lattice[0], lattice[1], lattice[2]

In [135]:
XGChi0.Vis_tool(chi0rrvs, Rvs, Avs, Bvs, Cvs, ngkpt, natomvs, xredvs, N=10000, isomin=0)